In [1]:
import json
import pandas as pd
import re
import glob
import os
import numpy as np
import tzlocal
from datetime import datetime
from pandas.io.json import json_normalize
from IPython.display import display, HTML

/home/marina/anaconda3/lib/python3.6/importlib/_bootstrap.py:219: RuntimeWarning: numpy.dtype size changed, may indicate binary incompatibility. Expected 96, got 88
  return f(*args, **kwds)
/home/marina/anaconda3/lib/python3.6/importlib/_bootstrap.py:219: RuntimeWarning: numpy.dtype size changed, may indicate binary incompatibility. Expected 96, got 88
  return f(*args, **kwds)


# Reading all available data
Reading all available data from the folder *.\data* in the venv. After that, we are sparsying it in order to keep it in json format. Finally, *json_sensors* is the list of all jsons.

In [2]:
def readFiles():
    all_files = []
    #list_of_files = os.listdir('./data/')
    #print(list_of_files[0:4])
    for file_name in glob.glob("./data/*"):
            f = open(file_name, 'r') #./data/01-003-0093cl
            all_files.append(f.readlines())
            f.close()
    return all_files

In [3]:
def sparseJSON(all_files):
    all_len_data = 0
    json_sensors = []
    for index, element in enumerate(all_files):
        #print(index, element[0])
        #print(len(element))
        match_obj = re.findall(r"(\{\"sensors\":[\s\[\]\w\"\-:,\.\/]*\{[\s\[\]\w\"\-:,\.\/]*\}[\s\[\]\w\"\-:,\.\/]*"
                           r"\{[\s\[\]\w\"\-:,\.\/]*\{[\s\[\]\w\"\-:,\.\/]*\{[\s\[\]\w\"\-:,\.\/]*\}[\s\[\]\w\"\-:,\.\/]"
                           r"*\}\}\})", element[0], re.M)

        all_len_data = all_len_data + len(match_obj)

        #print("jsons of len {1}:{0}\n".format(match_obj, len(match_obj)))
        #print("one piece = ", (match_obj[0]))

        for obj in match_obj:
            json_sensors.append(json.loads(obj))
        #print(json_sensors[35]['sensors'])
    #print(all_len_data)
    return(json_sensors)

# Processing data and Statistics

In [4]:
def processDataFrame(json_sensors):
    df = pd.DataFrame.from_dict(json_normalize(json_sensors), orient='columns')
    #print(df)

    df.columns = ['message_destination', 'message_payload_rssi', 'message_payload_suData_bat',
                  'message_payload_suData_sensor_config', 'message_payload_suData_temp', 'message_payload_suID',
                  'receiverid', 'request_responseTime', 'request_status', 'sensors', 'timestamp']
    #print(str(df.dtypes))
    df['sensors'] = df['sensors'].astype('str')
    for i in range(len(df.sensors)):
        df.at[i, 'sensors'] = df.at[i, 'sensors'][2:-2]
    print(df.dtypes)
    return(df)

def printStats(df):
    #print("object:", df.select_dtypes(include='object'))
    floats = df.select_dtypes(include='float64')
    objects = df.select_dtypes(include='object')
    #print(floats.columns.tolist())
    print("\nStatistics of the columns:\n")
    for col_name in floats.columns.tolist():
        print(df[col_name].describe())
    print("\nUnique values of the columns:\n")
    for col_name in objects.columns.tolist():
        un = df[col_name].unique()
        print(len(un), un)

# Running code window

jupyter notebook --NotebookApp.iopub_data_rate_limit=10000000000

In [5]:
all_files = readFiles()
json_sensors = sparseJSON(all_files)
print("len of json_sensors=", len(json_sensors))
print("type of data json_sensors =", type(json_sensors[0])) # array of dictionaries


#df_sensors = pd.DataFrame.from_dict(json_sensors, orient='columns')

len of json_sensors= 17323
type of data json_sensors = <class 'dict'>


Putting data into data frame in order to make some exploratory analysis of data.

In [31]:
df = processDataFrame(json_sensors)

message_destination                      object
message_payload_rssi                    float64
message_payload_suData_bat              float64
message_payload_suData_sensor_config    float64
message_payload_suData_temp             float64
message_payload_suID                     object
receiverid                               object
request_responseTime                    float64
request_status                          float64
sensors                                  object
timestamp                               float64
dtype: object


In [32]:
display(df.head(10))


message_destination  message_payload_rssi  \
0  v1/rec/02-004-0001/suStatus                  -6.0   
1  v1/rec/02-004-0001/suStatus                  -6.0   
2  v1/rec/02-004-0001/suStatus                 -16.0   
3  v1/rec/02-004-0001/suStatus                 -12.0   
4  v1/rec/02-004-0001/suStatus                  -3.0   
5  v1/rec/02-004-0001/suStatus                  -6.0   
6  v1/rec/02-004-0001/suStatus                 -18.0   
7  v1/rec/02-004-0001/suStatus                 -15.0   
8  v1/rec/02-004-0001/suStatus                  -4.0   
9  v1/rec/02-004-0001/suStatus                 -15.0   

   message_payload_suData_bat  message_payload_suData_sensor_config  \
0                      2960.0                                 192.0   
1                      3007.0                                 192.0   
2                      2960.0                                 192.0   
3                      3007.0                                 192.0   
4                      3007.0                                 192.0   
5                      2960.0                                 192.0   
6                      2960.0                                 192.0   
7                      3007.0                                 192.0   
8                      2960.0                                 192.0   
9                      2960.0                                 192.0   

   message_payload_suData_temp message_payload_suID   receiverid  \
0                         23.0          01-003-0052  02-004-0001   
1                         23.0          01-003-0052  02-004-0001   
2                         23.0          01-003-0052  02-004-0001   
3                         20.0          01-003-0052  02-004-0001   
4                         23.0          01-003-0052  02-004-0001   
5                         23.0          01-003-0052  02-004-0001   
6                         23.0          01-003-0052  02-004-0001   
7                         20.0          01-003-0052  02-004-0001   
8                         23.0          01-003-0052  02-004-0001   
9                         23.0          01-003-0052  02-004-0001   

   request_responseTime  request_status      sensors     timestamp  
0             92.814207           200.0  01-003-0052  1.528701e+09  
1            106.623888           200.0  01-003-0052  1.528702e+09  
2             99.778414           200.0  01-003-0052  1.528697e+09  
3            108.108044           200.0  01-003-0052  1.528697e+09  
4             92.387676           200.0  01-003-0052  1.528700e+09  
5             95.406294           200.0  01-003-0052  1.528701e+09  
6             93.272448           200.0  01-003-0052  1.528697e+09  
7            108.892679           200.0  01-003-0052  1.528699e+09  
8            106.695890           200.0  01-003-0052  1.528701e+09  
9            100.328922           200.0  01-003-0052  1.528699e+09

In [33]:
printStats(df)



Statistics of the columns:

count    17323.000000
mean       -11.463776
std          7.803927
min        -21.000000
25%        -19.000000
50%        -13.000000
75%         -6.000000
max          9.000000
Name: message_payload_rssi, dtype: float64
count    17323.000000
mean      2999.233389
std         33.588162
min       2839.000000
25%       2976.000000
50%       3007.000000
75%       3019.000000
max       3066.000000
Name: message_payload_suData_bat, dtype: float64
count    17323.0
mean       192.0
std          0.0
min        192.0
25%        192.0
50%        192.0
75%        192.0
max        192.0
Name: message_payload_suData_sensor_config, dtype: float64
count    17323.000000
mean        22.540091
std          3.974306
min         14.000000
25%         20.000000
50%         23.000000
75%         24.000000
max         37.000000
Name: message_payload_suData_temp, dtype: float64
count    17323.000000
mean       100.885306
std         71.133281
min         81.160069
25%         92.305

In [7]:
def getTime(timestamp):

    unix_timestamp = float(timestamp) #float("1533111600")
    local_timezone = tzlocal.get_localzone()  # get pytz timezone
    local_time = datetime.fromtimestamp(unix_timestamp, local_timezone)

    # To display it, you could use any time format that is supported by your system e.g.:

    #print(local_time.strftime("%Y-%m-%d %H:%M:%S (%Z)"))#.%f%z (%Z)"))
    #print(local_time.strftime("%B %d %Y"))
    return(local_time.strftime("%Y-%m-%d %H:%M:%S (%Z)"))#.%f%z (%Z)"))
def differenceTime(diff_timestamp):
    from datetime import datetime
    date_format = "%Y-%m-%d %H:%M:%S (%Z)"
    a = datetime.strptime('1970-01-01 01:00:00 (CET)', date_format)
    b = datetime.strptime(getTime(diff_timestamp), date_format)
    delta = b - a
    return(delta)

getTime(1533111600.0)

'2018-08-01 10:20:00 (CEST)'

In [34]:
def changeTimestamp(df, stringFrom, stringTo):
    df[stringTo] =  df[stringFrom].astype('str')    
    for i in range(len(df[stringTo])):        
        df.at[i, stringTo] = getTime(df.at[i, stringTo])
    return df  
        

In [35]:
df  = changeTimestamp(df, 'timestamp', 'time_std')
display(df.head(3))


message_destination  message_payload_rssi  \
0  v1/rec/02-004-0001/suStatus                  -6.0   
1  v1/rec/02-004-0001/suStatus                  -6.0   
2  v1/rec/02-004-0001/suStatus                 -16.0   

   message_payload_suData_bat  message_payload_suData_sensor_config  \
0                      2960.0                                 192.0   
1                      3007.0                                 192.0   
2                      2960.0                                 192.0   

   message_payload_suData_temp message_payload_suID   receiverid  \
0                         23.0          01-003-0052  02-004-0001   
1                         23.0          01-003-0052  02-004-0001   
2                         23.0          01-003-0052  02-004-0001   

   request_responseTime  request_status      sensors     timestamp  \
0             92.814207           200.0  01-003-0052  1.528701e+09   
1            106.623888           200.0  01-003-0052  1.528702e+09   
2             99.778414           200.0  01-003-0052  1.528697e+09   

                     time_std  
0  2018-06-11 09:07:38 (CEST)  
1  2018-06-11 09:32:38 (CEST)  
2  2018-06-11 08:10:47 (CEST)

## SQL queries on data to see data structure

In [36]:
gb = df.groupby(['sensors', 'receiverid'])
#gb.groups
##gb.<TAB>

In [38]:
pd.DataFrame(gb.mean()).reset_index().head(5)
#gb.size()# count ans size are the same

sensors   receiverid  message_payload_rssi  message_payload_suData_bat  \
0  01-003-0014  02-004-0000            -12.386997                 2976.000000   
1  01-003-0016  02-004-0003            -18.112266                 3019.000000   
2  01-003-0019  02-004-0007              3.530139                 2957.142195   
3  01-003-001C  02-004-0003            -19.347339                 3018.759104   
4  01-003-0022  02-004-0003            -19.783019                 3007.000000   

   message_payload_suData_sensor_config  message_payload_suData_temp  \
0                                 192.0                    28.113003   
1                                 192.0                    21.062370   
2                                 192.0                    21.432767   
3                                 192.0                    26.000000   
4                                 192.0                    17.000000   

   request_responseTime  request_status     timestamp  
0            109.242910           200.0  1.528700e+09  
1            100.360608           200.0  1.528699e+09  
2            100.340799           200.0  1.528700e+09  
3             99.032168           200.0  1.528699e+09  
4            102.177482           200.0  1.528700e+09

In [39]:
pd.DataFrame({'count' : df.groupby( ['sensors', 'receiverid'] ).size()}).reset_index().head(5)

sensors   receiverid  count
0  01-003-0014  02-004-0000    646
1  01-003-0016  02-004-0003    481
2  01-003-0019  02-004-0007    647
3  01-003-001C  02-004-0003    357
4  01-003-0022  02-004-0003    212

In [41]:
display(df[['sensors', 'receiverid','message_payload_rssi']].head(5)) # like select
df_select =  df[['sensors', 'receiverid','message_payload_rssi', 'timestamp', 'time_std']]#.head(5) # like select

sensors   receiverid  message_payload_rssi
0  01-003-0052  02-004-0001                  -6.0
1  01-003-0052  02-004-0001                  -6.0
2  01-003-0052  02-004-0001                 -16.0
3  01-003-0052  02-004-0001                 -12.0
4  01-003-0052  02-004-0001                  -3.0

In [64]:
display(df_select.groupby( ['sensors', 'receiverid'] ).min().head(5))
display(df_select.groupby( ['sensors', 'receiverid'] ).max().head(5))

message_payload_rssi     timestamp
sensors     receiverid                                     
01-003-0014 02-004-0000                 -18.0  1.528697e+09
01-003-0016 02-004-0003                 -21.0  1.528697e+09
01-003-0019 02-004-0007                 -15.0  1.528697e+09
01-003-001C 02-004-0003                 -21.0  1.528697e+09
01-003-0022 02-004-0003                 -21.0  1.528697e+09

message_payload_rssi     timestamp
sensors     receiverid                                     
01-003-0014 02-004-0000                  -7.0  1.528703e+09
01-003-0016 02-004-0003                 -12.0  1.528703e+09
01-003-0019 02-004-0007                   7.0  1.528703e+09
01-003-001C 02-004-0003                 -16.0  1.528703e+09
01-003-0022 02-004-0003                 -17.0  1.528703e+09

In [70]:
df_select.groupby( ['sensors', 'receiverid'] ).agg({'message_payload_rssi': [np.min, np.max]}).reset_index().head(15)

sensors   receiverid     timestamp message_payload_rssi      
                                                           amin  amax
0   01-003-0033  02-004-0000  1.528697e+09                 -6.0  -6.0
1   01-003-0092  02-004-0007  1.528697e+09                -16.0 -16.0
2   01-003-0042  02-004-0007  1.528697e+09                -16.0 -16.0
3   01-003-0039  02-004-0003  1.528697e+09                -19.0 -19.0
4   01-003-0095  02-004-0007  1.528697e+09                 -8.0  -8.0
5   01-003-005C  02-004-0003  1.528697e+09                -20.0 -20.0
6   01-003-001C  02-004-0003  1.528697e+09                -17.0 -17.0
7   01-003-0086  02-004-0003  1.528697e+09                -19.0 -19.0
8   01-003-002E  02-004-0003  1.528697e+09                -20.0 -20.0
9   01-003-006B  02-004-0000  1.528697e+09                -10.0 -10.0
10  01-003-0052  02-004-0001  1.528697e+09                 -9.0  -9.0
11  01-003-0062  02-004-0007  1.528697e+09                -18.0 -18.0
12  01-003-0038  02-004-0003  1.528697e+09                -20.0 -20.0
13  01-003-0078  02-004-0003  1.528697e+09                -17.0 -17.0
14  01-003-0058  02-004-0003  1.528697e+09                -20.0 -20.0

In [73]:
df_select.groupby( ['sensors', 'receiverid'] ).agg({'timestamp': [np.min, np.max]}).reset_index().head(15)

sensors   receiverid     timestamp              
                                      amin          amax
0   01-003-0014  02-004-0000  1.528697e+09  1.528703e+09
1   01-003-0016  02-004-0003  1.528697e+09  1.528703e+09
2   01-003-0019  02-004-0007  1.528697e+09  1.528703e+09
3   01-003-001C  02-004-0003  1.528697e+09  1.528703e+09
4   01-003-0022  02-004-0003  1.528697e+09  1.528703e+09
5   01-003-0022  02-004-0007  1.528697e+09  1.528703e+09
6   01-003-0029  02-004-0000  1.528697e+09  1.528703e+09
7   01-003-002A  02-004-0003  1.528697e+09  1.528703e+09
8   01-003-002A  02-004-0007  1.528697e+09  1.528703e+09
9   01-003-002E  02-004-0003  1.528697e+09  1.528703e+09
10  01-003-0030  02-004-0006  1.528702e+09  1.528703e+09
11  01-003-0033  02-004-0000  1.528697e+09  1.528703e+09
12  01-003-0038  02-004-0003  1.528697e+09  1.528703e+09
13  01-003-0039  02-004-0003  1.528697e+09  1.528702e+09
14  01-003-0042  02-004-0003  1.528699e+09  1.528703e+09

In [163]:
df_select.sort_values(['sensors','timestamp']).reset_index().head(5)

index      sensors   receiverid  message_payload_rssi     timestamp  \
0   1381  01-003-0014  02-004-0000                 -18.0  1.528697e+09   
1   1367  01-003-0014  02-004-0000                 -17.0  1.528697e+09   
2   1464  01-003-0014  02-004-0000                 -18.0  1.528697e+09   
3   1239  01-003-0014  02-004-0000                 -18.0  1.528697e+09   
4   1776  01-003-0014  02-004-0000                 -18.0  1.528697e+09   

                     time_std  
0  2018-06-11 07:55:30 (CEST)  
1  2018-06-11 07:55:40 (CEST)  
2  2018-06-11 07:55:50 (CEST)  
3  2018-06-11 07:56:00 (CEST)  
4  2018-06-11 07:56:10 (CEST)

In [167]:
print("Dataframe 2:")
display(HTML(df_select.sort_values(['sensors','timestamp']).reset_index().to_html()))

Dataframe 2:


### Difference between Timestamps

In this small section I wrote a function that will shoe the difference between two timestamps grouped by *sensors, receiverid*.
After that there is displayed unique time difference just in order to show the function how to write it.


In [10]:
def findTimeDifferenceDataFrame(df):
    df['diff'] = df.groupby(by=['sensors', 'receiverid'])['timestamp'].transform(lambda x: x.max() - x.min())
    select_diff = df[['sensors', 'receiverid', 'message_payload_rssi', 'timestamp', 'time_std', 'diff']]
    return select_diff

In [43]:
select_diff  = findTimeDifferenceDataFrame(df)
display(df.head(3))
print("_________________________________________________________________________\n")
print("Unique time differences for every sensor's message received by a receiver")
print("_________________________________________________________________________")
display(select_diff.groupby(['sensors', 'receiverid'])['diff'].unique())
    

message_destination  message_payload_rssi  \
0  v1/rec/02-004-0001/suStatus                  -6.0   
1  v1/rec/02-004-0001/suStatus                  -6.0   
2  v1/rec/02-004-0001/suStatus                 -16.0   

   message_payload_suData_bat  message_payload_suData_sensor_config  \
0                      2960.0                                 192.0   
1                      3007.0                                 192.0   
2                      2960.0                                 192.0   

   message_payload_suData_temp message_payload_suID   receiverid  \
0                         23.0          01-003-0052  02-004-0001   
1                         23.0          01-003-0052  02-004-0001   
2                         23.0          01-003-0052  02-004-0001   

   request_responseTime  request_status      sensors     timestamp  \
0             92.814207           200.0  01-003-0052  1.528701e+09   
1            106.623888           200.0  01-003-0052  1.528702e+09   
2             99.778414           200.0  01-003-0052  1.528697e+09   

                     time_std         diff  
0  2018-06-11 09:07:38 (CEST)  6471.543738  
1  2018-06-11 09:32:38 (CEST)  6471.543738  
2  2018-06-11 08:10:47 (CEST)  6471.543738

_________________________________________________________________________

Unique time differences for every sensor's message received by a receiver
_________________________________________________________________________


sensors      receiverid 
01-003-0014  02-004-0000      [6461.50922369957]
01-003-0016  02-004-0003     [6391.588057279587]
01-003-0019  02-004-0007     [6461.606385707855]
01-003-001C  02-004-0003     [6471.546736955643]
01-003-0022  02-004-0003    [6411.3580820560455]
             02-004-0007      [6461.07563495636]
01-003-0029  02-004-0000     [6461.588096857071]
01-003-002A  02-004-0003     [6461.687522411346]
             02-004-0007     [6461.687367200851]
01-003-002E  02-004-0003     [6461.627290964127]
01-003-0030  02-004-0006     [610.1429855823517]
01-003-0033  02-004-0000     [6471.563055515289]
01-003-0038  02-004-0003     [6471.563903331757]
01-003-0039  02-004-0003     [5941.502511978149]
01-003-0042  02-004-0003     [3680.698176383972]
             02-004-0007       [6441.6051197052]
01-003-004A  02-004-0001     [6461.626160621643]
01-003-0052  02-004-0001     [6471.543737888336]
01-003-0058  02-004-0003     [6463.981488227844]
01-003-005A  02-004-0003     [6121.557210922

### Data with which it is possible to work

Here we can see that the data is even that's why we can use either mean or median to represent *rssi*. I would choose median, as it is easier to work with it.

In [44]:
def changeDifferenceInTime(df, stringFrom, stringTo):
    #df = df.assign(time_std = df[stringFrom])
    df[stringTo] =  df[stringFrom].astype('str')    
    for i in range(len(df[stringTo])):        
        df.at[i, stringTo] = differenceTime(df.at[i, stringTo])
    return df     
        
    
def rssiDataFrame(df):
    print("_______________________________________________________________________\n")
    print("\t\tMain RSSI table")
    print("_______________________________________________________________________")
    select_diff = findTimeDifferenceDataFrame(df)
    result_df = select_diff.groupby(['sensors', 'receiverid']).agg(
        {'message_payload_rssi': [np.min, np.max, np.median], 'diff': np.max,
         'timestamp': [np.min, np.max]}).reset_index()
    my_dict_result = {'sensors': result_df.sensors,
                      'receiverid': result_df.receiverid,
                      'message_payload_rssi_min': result_df.message_payload_rssi.amin,
                      'message_payload_rssi_max': result_df.message_payload_rssi.amax,
                      'message_payload_rssi_median': result_df.message_payload_rssi['median'],
                      'diff': result_df['diff'].amax,
                      'timestamp_min': result_df['timestamp'].amin,
                      'timestamp_max': result_df['timestamp'].amax}
    df_result = pd.DataFrame(data=my_dict_result)
    df_result = changeTimestamp(df_result, 'timestamp_min', 'time_std_min')
    df_result = changeTimestamp(df_result, 'timestamp_max', 'time_std_max')
    df_result = changeDifferenceInTime(df_result, 'diff', 'time_diff')


    return df_result

In [45]:
df_rssi = rssiDataFrame(df)
display(df_rssi)

_______________________________________________________________________

		Main RSSI table
_______________________________________________________________________


sensors   receiverid  message_payload_rssi_min  \
0   01-003-0014  02-004-0000                     -18.0   
1   01-003-0016  02-004-0003                     -21.0   
2   01-003-0019  02-004-0007                     -15.0   
3   01-003-001C  02-004-0003                     -21.0   
4   01-003-0022  02-004-0003                     -21.0   
5   01-003-0022  02-004-0007                     -18.0   
6   01-003-0029  02-004-0000                       0.0   
7   01-003-002A  02-004-0003                     -21.0   
8   01-003-002A  02-004-0007                     -19.0   
9   01-003-002E  02-004-0003                     -21.0   
10  01-003-0030  02-004-0006                     -20.0   
11  01-003-0033  02-004-0000                     -13.0   
12  01-003-0038  02-004-0003                     -21.0   
13  01-003-0039  02-004-0003                     -21.0   
14  01-003-0042  02-004-0003                     -21.0   
15  01-003-0042  02-004-0007                     -21.0   
16  01-003-004A  02-004-0001                     -12.0   
17  01-003-0052  02-004-0001                     -18.0   
18  01-003-0058  02-004-0003                     -21.0   
19  01-003-005A  02-004-0003                     -21.0   
20  01-003-005C  02-004-0003                     -21.0   
21  01-003-005F  02-004-0003                     -21.0   
22  01-003-0060  02-004-0001                      -3.0   
23  01-003-0062  02-004-0003                     -21.0   
24  01-003-0062  02-004-0007                     -20.0   
25  01-003-0064  02-004-0003                     -21.0   
26  01-003-0067  02-004-0003                     -21.0   
27  01-003-006B  02-004-0000                     -13.0   
28  01-003-006B  02-004-0001                     -20.0   
29  01-003-006C  02-004-0003                     -21.0   
30  01-003-0078  02-004-0003                     -21.0   
31  01-003-0081  02-004-0003                     -21.0   
32  01-003-0085  02-004-0003                     -21.0   
33  01-003-0086  02-004-0003                     -21.0   
34  01-003-0088  02-004-0003                     -21.0   
35  01-003-0088  02-004-0007                     -19.0   
36  01-003-0089  02-004-0003                     -21.0   
37  01-003-008C  02-004-0003                     -21.0   
38  01-003-0092  02-004-0003                     -21.0   
39  01-003-0092  02-004-0007                     -20.0   
40  01-003-0093  02-004-0003                     -21.0   
41  01-003-0093  02-004-0007                     -21.0   
42  01-003-0094  02-004-0003                     -21.0   
43  01-003-0095  02-004-0003                     -21.0   
44  01-003-0095  02-004-0007                     -20.0   

    message_payload_rssi_max  message_payload_rssi_median         diff  \
0                       -7.0                        -12.0  6461.509224   
1                      -12.0                        -19.0  6391.588057   
2                        7.0                          4.0  6461.606386   
3                      -16.0                        -20.0  6471.546737   
4                      -17.0                        -20.0  6411.358082   
5                       -3.0                         -6.0  6461.075635   
6                        3.0                          1.0  6461.588097   
7                      -12.0                        -19.0  6461.687522   
8                       -4.0                        -11.0  6461.687367   
9                      -19.0                        -20.0  6461.627291   
10                     -20.0                        -20.0   610.142986   
11                       0.0                         -2.0  6471.563056   
12                     -18.0                        -20.0  6471.563903   
13                     -12.0                        -18.0  5941.502512   
14                     -20.0                        -20.5  3680.698176   
15                      -7.0                        -14.0  6441.605120   
16                       4.0                          1.0  6461.626161   
17     

### Transform min and max timespan to real time

In [12]:
def changeTimestampString(df, stringFrom, stringTo):
    #df = df.assign(time_std = df[stringFrom])
    df[stringTo] =  df[stringFrom].astype('str')    
    for i in range(len(df[stringTo])):        
        df.at[i, stringTo] = getTime(df.at[i, stringTo])
    return df  

def findTimeDifferenceDataFrame(df):
    df['diff'] = df.groupby(by=['sensors', 'receiverid'])['timestamp'].transform(lambda x: x.max() - x.min())
    select_diff = df[['sensors', 'receiverid', 'message_payload_rssi', 'timestamp', 'time_std', 'diff']]
    return select_diff

def minMaxTimeDataFrame(df):
    print("_______________________________________________________________________\n")
    print("Min and max time when every sensor's message was received by a receiver")
    print("_______________________________________________________________________")
    select_diff = findTimeDifferenceDataFrame(df)
    timestamps_df = select_diff.groupby(['sensors', 'receiverid']).agg(
        {'timestamp': [np.min, np.max]}).reset_index()
    dict_timestamps = {'sensors': timestamps_df.sensors,
                       'receiverid': timestamps_df.receiverid,
                       'timestamp_min': timestamps_df['timestamp'].amin,
                       'timestamp_max': timestamps_df['timestamp'].amax}

    new_timestamps = pd.DataFrame(data=dict_timestamps)
    new_timestamps = changeTimestampString(new_timestamps, 'timestamp_min', 'time_std_min')
    new_timestamps = changeTimestampString(new_timestamps, 'timestamp_max', 'time_std_max')

    return(new_timestamps)

In [19]:
display(minMaxTimeDataFrame(df))

_______________________________________________________________________

Min and max time when every sensor's message was received by a receiver
_______________________________________________________________________


sensors   receiverid  timestamp_min  timestamp_max  \
0   01-003-0014  02-004-0000   1.528697e+09   1.528703e+09   
1   01-003-0016  02-004-0003   1.528697e+09   1.528703e+09   
2   01-003-0019  02-004-0007   1.528697e+09   1.528703e+09   
3   01-003-001C  02-004-0003   1.528697e+09   1.528703e+09   
4   01-003-0022  02-004-0003   1.528697e+09   1.528703e+09   
5   01-003-0022  02-004-0007   1.528697e+09   1.528703e+09   
6   01-003-0029  02-004-0000   1.528697e+09   1.528703e+09   
7   01-003-002A  02-004-0003   1.528697e+09   1.528703e+09   
8   01-003-002A  02-004-0007   1.528697e+09   1.528703e+09   
9   01-003-002E  02-004-0003   1.528697e+09   1.528703e+09   
10  01-003-0030  02-004-0006   1.528702e+09   1.528703e+09   
11  01-003-0033  02-004-0000   1.528697e+09   1.528703e+09   
12  01-003-0038  02-004-0003   1.528697e+09   1.528703e+09   
13  01-003-0039  02-004-0003   1.528697e+09   1.528702e+09   
14  01-003-0042  02-004-0003   1.528699e+09   1.528703e+09   
15  01-003-0042  02-004-0007   1.528697e+09   1.528703e+09   
16  01-003-004A  02-004-0001   1.528697e+09   1.528703e+09   
17  01-003-0052  02-004-0001   1.528697e+09   1.528703e+09   
18  01-003-0058  02-004-0003   1.528697e+09   1.528703e+09   
19  01-003-005A  02-004-0003   1.528697e+09   1.528703e+09   
20  01-003-005C  02-004-0003   1.528697e+09   1.528703e+09   
21  01-003-005F  02-004-0003   1.528698e+09   1.528703e+09   
22  01-003-0060  02-004-0001   1.528697e+09   1.528703e+09   
23  01-003-0062  02-004-0003   1.528697e+09   1.528703e+09   
24  01-003-0062  02-004-0007   1.528697e+09   1.528703e+09   
25  01-003-0064  02-004-0003   1.528698e+09   1.528703e+09   
26  01-003-0067  02-004-0003   1.528698e+09   1.528703e+09   
27  01-003-006B  02-004-0000   1.528697e+09   1.528703e+09   
28  01-003-006B  02-004-0001   1.528697e+09   1.528697e+09   
29  01-003-006C  02-004-0003   1.528697e+09   1.528702e+09   
30  01-003-0078  02-004-0003   1.528697e+09   1.528703e+09   
31  01-003-0081  02-004-0003   1.528698e+09   1.528703e+09   
32  01-003-0085  02-004-0003   1.528697e+09   1.528703e+09   
33  01-003-0086  02-004-0003   1.528697e+09   1.528703e+09   
34  01-003-0088  02-004-0003   1.528697e+09   1.528703e+09   
35  01-003-0088  02-004-0007   1.528697e+09   1.528700e+09   
36  01-003-0089  02-004-0003   1.528698e+09   1.528703e+09   
37  01-003-008C  02-004-0003   1.528698e+09   1.528703e+09   
38  01-003-0092  02-004-0003   1.528697e+09   1.528703e+09   
39  01-003-0092  02-004-0007   1.528697e+09   1.528703e+09   
40  01-003-0093  02-004-0003   1.528698e+09   1.528703e+09   
41  01-003-0093  02-004-0007   1.528697e+09   1.528703e+09   
42  01-003-0094  02-004-0003   1.528697e+09   1.528703e+09   
43  01-003-0095  02-004-0003   1.528697e+09   1.528703e+09   
44  01-003-0095  02-004-0007   1.528697e+09   1.528703e+09   

                  time_std_min                time_std_max  
0   2018-06-11 07:55:30 (CEST)  2018-06-11 09:43:11 (CEST)  
1   2018-06-11 07:55:34 (CEST)  2018-06-11 09:42:06 (CEST)  
2   2018-06-11 07:55:33 (CEST)  2018-06-11 09:43:14 (CEST)  
3   2018-06-11 07:55:25 (CEST)  2018-06-11 09:43:17 (CEST)  
4   2018-06-11 07:55:54 (CEST)  2018-06-11 09:42:45 (CEST)  
5   2018-06-11 07:55:34 (CEST)  2018-06-11 09:43:15 (CEST)  
6   2018-06-11 07:55:33 (CEST)  2018-06-11 09:43:14 (CEST)  
7   2018-06-11 07:55:31 (CEST)  2018-06-11 09:43:13 (CEST)  
8   2018-06-11 07:55:31 (CEST)  2018-06-11 09:43:13 (CEST)  
9   2018-06-11 07:55:26 (CEST)  2018-06-11 09:43:08 (CEST)  
10  2018-06-11 09:30:15 (CEST)  2018-06-11 09:40:25 (CEST)  
11  2018-06-11 07:55:24 (CEST)  2018-06-11 09:43:15 (CEST)  
12  2018-06-11 07:55:28 (CEST)  2018-06-11 09:43:19 (CEST)  
13  2018-06-11 07:55:25 (CEST)  2018-06-11 09:34:26 (CEST)  
14  2018-06-11 08:40:55 (CEST)  2018-06-11 09:42:16 (CEST)  
15  2018-06-11 07:55:24 (CEST)  2018-06-11 09:42:46 (CEST)  
16  2018-06-11 07:55:32 (CEST)  2018-06-11 09:43:14 (CEST)  
17  2018-06-11 07:55:27 (CEST)  2018-06-11 09:43:18 (CEST

For a chosen sensor unit and a receiver we will look onto timing with wich the rssi was sent. In other words we will onto it's change over every 10 seconds ( or more).

In [47]:
df_small = df[df['sensors'] == '01-003-0014'].reset_index()
df_small = df_small.sort_values(['timestamp'])
df_small['seconds'] =(df_small['timestamp'] - df_small['timestamp'].min()).round()

In [48]:
display(df_small)

index          message_destination  message_payload_rssi  \
176   1381  v1/rec/02-004-0000/suStatus                 -18.0   
162   1367  v1/rec/02-004-0000/suStatus                 -17.0   
259   1464  v1/rec/02-004-0000/suStatus                 -18.0   
34    1239  v1/rec/02-004-0000/suStatus                 -18.0   
571   1776  v1/rec/02-004-0000/suStatus                 -18.0   
141   1346  v1/rec/02-004-0000/suStatus                 -17.0   
239   1444  v1/rec/02-004-0000/suStatus                 -18.0   
448   1653  v1/rec/02-004-0000/suStatus                 -18.0   
75    1280  v1/rec/02-004-0000/suStatus                 -18.0   
92    1297  v1/rec/02-004-0000/suStatus                 -17.0   
597   1802  v1/rec/02-004-0000/suStatus                 -17.0   
253   1458  v1/rec/02-004-0000/suStatus                 -17.0   
594   1799  v1/rec/02-004-0000/suStatus                 -18.0   
283   1488  v1/rec/02-004-0000/suStatus                 -18.0   
205   1410  v1/rec/02-004-0000/suStatus                 -18.0   
5     1210  v1/rec/02-004-0000/suStatus                 -18.0   
360   1565  v1/rec/02-004-0000/suStatus                 -18.0   
335   1540  v1/rec/02-004-0000/suStatus                 -18.0   
214   1419  v1/rec/02-004-0000/suStatus                 -18.0   
161   1366  v1/rec/02-004-0000/suStatus                 -16.0   
235   1440  v1/rec/02-004-0000/suStatus                 -17.0   
190   1395  v1/rec/02-004-0000/suStatus                 -18.0   
13    1218  v1/rec/02-004-0000/suStatus                 -16.0   
137   1342  v1/rec/02-004-0000/suStatus                 -16.0   
292   1497  v1/rec/02-004-0000/suStatus                 -14.0   
123   1328  v1/rec/02-004-0000/suStatus                 -16.0   
255   1460  v1/rec/02-004-0000/suStatus                 -14.0   
133   1338  v1/rec/02-004-0000/suStatus                 -14.0   
631   1836  v1/rec/02-004-0000/suStatus                 -14.0   
475   1680  v1/rec/02-004-0000/suStatus                 -14.0   
..     ...                          ...                   ...   
31    1236  v1/rec/02-004-0000/suStatus                 -12.0   
163   1368  v1/rec/02-004-0000/suStatus                 -13.0   
83    1288  v1/rec/02-004-0000/suStatus                 -13.0   
172   1377  v1/rec/02-004-0000/suStatus                 -13.0   
140   1345  v1/rec/02-004-0000/suStatus                 -13.0   
640   1845  v1/rec/02-004-0000/suStatus                 -14.0   
139   1344  v1/rec/02-004-0000/suStatus                 -14.0   
279   1484  v1/rec/02-004-0000/suStatus                 -13.0   
169   1374  v1/rec/02-004-0000/suStatus                 -13.0   
98    1303  v1/rec/02-004-0000/suStatus                 -13.0   
237   1442  v1/rec/02-004-0000/suStatus                 -13.0   
102   1307  v1/rec/02-004-0000/suStatus                 -13.0   
313   1518  v1/rec/02-004-0000/suStatus                 -13.0   
458   1663  v1/rec/02-004-0000/suStatus                 -13.0   
377   1582  v1/rec/02-004-0000/suStatus                 -13.0   
627   1832  v1/rec/02-004-0000/suStatus                 -13.0   
528   1733  v1/rec/02-004-0000/suStatus                 -13.0   
381   1586  v1/rec/02-004-0000/suStatus                 -13.0   
114   1319  v1/rec/02-004-0000/suStatus                 -13.0   
325   1530  v1/rec/02-004-0000/suStatus                 -12.0   
557   1762  v1/rec/02-004-0000/suStatus                 -14.0   
642   1847  v1/rec/02-004-0000/suStatus                 -13.0   
46    1251  v1/rec/02-004-0000/suStatus                 -14.0   
62    1267  v1/rec/02-004-0000/suStatus                 -13.0   
6     1211  v1/rec/02-004-0000/suStatus                 -14.0   
144   1349  v1/rec/02-004-0000/suStatus                 -15.0   
282   1487  v1/rec/02-004-0000/suStatus                 -14.0   
193   1398  v1/rec/02-004-0000/suStatus                 -13.0   
290   1495  v1/rec/02-004-0000/suStatus                 -14.0   
497   1702  v1/rec/02-004-0000/suStatus 